# Lab Instructions

Create 3 visualizations from a spatial and time-series dataset of your choice.  Describe your dataset including where it came from and the features it contains.  Each visualization should be accompanied by at least 1 - 2 sentences explaining how the features do (or do not!) change over time and througout space.

#%pip install statsmodels
import statsmodels.api as sm
import plotly.express as px
import plotly.io as pio

import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns

df = pd.read_csv('LegoSets.csv')

df_cleaned = df.dropna(subset=['USD_MSRP'])

print(f"Original Row Count: {len(df)}")
print(f"New Row Count: {len(df_cleaned)}")

df_cleaned.head()

df_cleaned.tail()

In [ ]:
#df_cleaned.to_csv('LegoSets_Cleaned.csv', index=False)

In [20]:
import pandas as pd
import plotly.express as px

df = pd.read_csv('ACPerCapita.csv')

# 1. Force the column to be numeric (turns text/errors into NaN)
df['alcohol consumption per capita (liters)'] = pd.to_numeric(
    df['alcohol consumption per capita (liters)'], 
    errors='coerce'
)

# 2. Fill NaN values with 0 (Fixes the "Invalid elements: [nan]" error)
df['alcohol consumption per capita (liters)'] = df['alcohol consumption per capita (liters)'].fillna(0)
# -------------------------------------

df.head()

Entity Code  Year  alcohol consumption per capita (liters)
0  Afghanistan  AFG  2010                                     0.21
1  Afghanistan  AFG  2015                                     0.21
2  Afghanistan  AFG  2018                                     0.21
3      Albania  ALB  2000                                     6.57
4      Albania  ALB  2005                                     7.65

In [21]:
df.tail()

Entity Code  Year  alcohol consumption per capita (liters)
989  Zimbabwe  ZWE  2000                                     2.46
990  Zimbabwe  ZWE  2005                                     2.77
991  Zimbabwe  ZWE  2010                                     3.93
992  Zimbabwe  ZWE  2015                                     4.92
993  Zimbabwe  ZWE  2018                                     4.67

In [22]:
fig = px.scatter(df, 
                  x="alcohol consumption per capita (liters)", 
                  y="Entity", 
                  animation_frame="Year",           
                  size="alcohol consumption per capita (liters)", 
                  color="Entity",                   
                  range_x=[0, 20], 
                  title="Distribution of Alcohol Consumption by Country (Animated)",
                  labels={'alcohol consumption per capita (liters)': 'Liters Per Capita'})

fig.update_layout(showlegend=False)
fig.layout.updatemenus[0].buttons[0].args[1]['frame']['duration'] = 1000 # Slower animation
fig.show()

Scatter Plot Distribution Spatially, the plot reflects the disparities between outliers in Eastern Europe with the highest levels of consumption and clusters in the Middle East with the lowest. The animated version of the plot suggests a trend, with developing countries moving to the right (higher consumption) over time and some western European countries moving to the left.

In [23]:
df.sort_values(by='Year', inplace=True)
apc_max = df['alcohol consumption per capita (liters)'].max()
apc_min = df['alcohol consumption per capita (liters)'].min()

fig = px.choropleth(df, 
                     locations="Code",                    
                     color='alcohol consumption per capita (liters)', 
                     hover_name="Entity", 
                     animation_frame="Year",              
                     color_continuous_scale=px.colors.sequential.Plasma,
                     range_color=[apc_min, apc_max],          
                     title="Global Alcohol Consumption Per Capita (Fixed Scale)")

fig.layout.updatemenus[0].buttons[0].args[1]['frame']['duration'] = 1000 # Slower animation

fig.show()

In [24]:
df['alcohol consumption per capita (liters)'].describe()

count    994.000000
mean       6.546932
std        7.894155
min        0.000000
25%        1.962500
50%        5.430000
75%        9.472500
max       98.000000
Name: alcohol consumption per capita (liters), dtype: float64

In [25]:
fig = px.choropleth(df, 
                     locations="Code",                    # Maps to ISO Codes
                     color="alcohol consumption per capita (liters)", 
                     hover_name="Entity", 
                     animation_frame="Year",              # <--- Animation Frame
                     color_continuous_scale=px.colors.sequential.Plasma,
                     range_color=[0, 10],                 # Fixed range prevents flickering colors
                     title="Global Alcohol Consumption Per Capita (Animated Map)")

fig.layout.updatemenus[0].buttons[0].args[1]['frame']['duration'] = 1000 # Slower animation

fig.show()

The map shows a "consumption belt" in Europe and Russia that separates the cultural low-consumption areas of North Africa and the Middle East. Over the years Western Europe has undergone a "cooling" trend (shown in the animation by dark colors becoming lighter). This trend may have been caused by successful public health campaigns.

In [26]:
run_df = pd.read_csv('world_marathon_majors.csv', encoding='ISO-8859-1')

run_df.head()

year              winner  gender   country      time marathon
0  2018      Dickson Chumba    Male     Kenya  02:05:30    Tokyo
1  2018      Birhane Dibaba  Female  Ethiopia  02:19:51    Tokyo
2  2017      Wilson Kipsang    Male     Kenya  02:03:58    Tokyo
3  2017  Sarah Chepchirchir  Female     Kenya  02:19:47    Tokyo
4  2016       Feyisa Lilesa    Male  Ethiopia  02:06:56    Tokyo

In [27]:
run_df['marathon'].value_counts()

marathon
Boston     175
NYC         92
Berlin      88
Chicago     80
London      77
Tokyo       24
Name: count, dtype: int64

In [28]:
run_df['country'].value_counts()


country
Kenya             136
United States     104
Ethiopia           51
Germany            36
United Kingdom     35
Japan              22
Norway             20
Canada             17
Portugal           11
Mexico             10
Finland            10
Russia              8
Poland              8
Brazil              7
Italy               6
South Africa        5
Belgium             5
New Zealand         5
Morocco             5
Tanzania            4
South Korea         3
Ireland             3
Australia           3
Colombia            2
Denmark             2
Switzerland         2
Romania             2
Sweden              2
Greece              2
Spain               2
Latvia              2
China               1
Hungary             1
Eritrea             1
Guatemala           1
Yugoslavia          1
Soviet Union        1
Name: count, dtype: int64

In [30]:
# 2. DATA PREPARATION (Converting "H:MM:SS" to Minutes)
def clean_time(t_str):
    try:
        parts = str(t_str).split(':')
        if len(parts) == 3:   # H:MM:SS
            return int(parts[0])*60 + int(parts[1]) + int(parts[2])/60
        elif len(parts) == 2: # MM:SS
            return int(parts[0])*60 + int(parts[1])/60
        return None
    except:
        return None

run_df['Time_Minutes'] = run_df['time'].apply(clean_time)

# 3. CREATE THE VISUALIZATION (Line Chart)
# We group by Year, Country, and Gender to handle years with multiple winners from same country
fig = px.line(run_df, 
              x="year", 
              y="Time_Minutes", 
              color="country",           # Spatial Distinction
              symbol="gender",           # Gender Distinction
              line_group="country",      # Connects the dots for each country
              hover_name="winner",
              hover_data=["marathon", "time"],
              markers=True,              # Adds dots to the lines
              title="Evolution of Winning Times by Country",
              labels={
                  "year": "Year", 
                  "Time_Minutes": "Winning Time (Minutes)", 
                  "country": "Country"
              })

# Reverse Y-Axis so "Faster" (lower time) is at the top
fig.update_layout(yaxis=dict(autorange="reversed"))

fig.show()

Evolution of Winning Times (Line Chart) Temporally, the lines generally trend upward (on the reversed axis), illustrating the consistent improvement in human performance and speed over the decades. Spatially, the color-coding distinguishes national origin, revealing how specific countries fair across all times.

In [31]:
import itertools

# 2. DEFINE LISTS: Get all unique values from your actual data
all_years = run_df['year'].unique()
all_marathons = run_df['marathon'].unique()
all_genders = run_df['gender'].dropna().unique() # Vital: Get 'Male' and 'Female'

# 3. CREATE SKELETON: All combinations of Year + Marathon + Gender
# This creates rows like: (2000, NYC, Male), (2000, NYC, Female)... for every year
skeleton = pd.DataFrame(
    list(itertools.product(all_years, all_marathons, all_genders)), 
    columns=['year', 'marathon', 'gender']
)

# 4. MERGE: Combine Skeleton with Real Data
# on=['year', 'marathon', 'gender'] ensures we map to the exact right rows
df_padded = pd.merge(skeleton, run_df, on=['year', 'marathon', 'gender'], how='left')

# 5. FILL NA: Critical Step!
# We must give the empty rows a valid Country so they have a place on the X-Axis
# (We leave 'Time_Minutes' as NaN so the point remains invisible)
df_padded['country'] = df_padded['country'].fillna(run_df['country'].iloc[0]) # Fill with any valid country name

# 6. PLOT
min_y = run_df['Time_Minutes'].min() - 2
max_y = run_df['Time_Minutes'].max() + 2

fig = px.scatter(df_padded, 
                 x="country", 
                 y="Time_Minutes", 
                 animation_frame="year",       
                 color="marathon",             
                 symbol="gender",              
                 hover_name="winner",
                 
                 # Force categories to be consistent
                 category_orders={
                     "country": sorted(list(run_df['country'].dropna().unique())),
                     "marathon": sorted(list(all_marathons))
                 },

                 range_y=[max_y, min_y], # Reversed Y-Axis (Faster is Higher)
                 size_max=15,
                 title="Winning Times Distribution by Country (Fixed Animation)",
                 labels={
                     "country": "Country", 
                     "Time_Minutes": "Winning Time (Minutes)",
                     "marathon": "Event"
                 })

fig.layout.updatemenus[0].buttons[0].args[1]['frame']['duration'] = 1000 # Slower animation

fig.show()

This display conveys the same content as above. However, as the animation progresses through time, the height of the points conveys the decreasing winning times across all majors in an era. The winning locations are visually encoded by the winning country columns: until the 1930s almost every win was from the US.

# End of Assignment
Everything below is trying to make year in chronological order.

In [32]:
# 1. Sort Data (as you were doing)
#run_df.sort_values(by='year', inplace=True)

# 2. DEFINE LISTS: Get all unique values from your actual data
all_years = run_df['year'].unique()
all_marathons = run_df['marathon'].unique()
all_genders = run_df['gender'].dropna().unique() # Vital: Get 'Male' and 'Female'

# 3. CREATE SKELETON: All combinations of Year + Marathon + Gender
# This creates rows like: (2000, NYC, Male), (2000, NYC, Female)... for every year
skeleton = pd.DataFrame(
    list(itertools.product(all_years, all_marathons, all_genders)), 
    columns=['year', 'marathon', 'gender']
)

# 4. MERGE: Combine Skeleton with Real Data
# on=['year', 'marathon', 'gender'] ensures we map to the exact right rows
df_padded = pd.merge(skeleton, run_df, on=['year', 'marathon', 'gender'], how='left')

# 5. FILL NA: Critical Step!
# We must give the empty rows a valid Country so they have a place on the X-Axis
# (We leave 'Time_Minutes' as NaN so the point remains invisible)
df_padded['country'] = df_padded['country'].fillna(run_df['country'].iloc[0]) # Fill with any valid country name

# 6. PLOT
min_y = run_df['Time_Minutes'].min() - 2
max_y = run_df['Time_Minutes'].max() + 2

fig = px.scatter(df_padded, 
                 x="country", 
                 y="Time_Minutes", 
                 animation_frame="year",       
                 color="marathon",             
                 symbol="gender",              
                 hover_name="winner",
                 
                 # Force categories to be consistent
                 category_orders={
                     "country": sorted(list(run_df['country'].dropna().unique())),
                     "marathon": sorted(list(all_marathons))
                 },

                 range_y=[max_y, min_y], # Reversed Y-Axis (Faster is Higher)
                 size_max=15,
                 title="Winning Times Distribution by Country (Fixed Animation)",
                 labels={
                     "country": "Country", 
                     "Time_Minutes": "Winning Time (Minutes)",
                     "marathon": "Event"
                 })

fig.layout.updatemenus[0].buttons[0].args[1]['frame']['duration'] = 1000 # Slower animation

fig.show()

In [33]:
# 1. SORT THE YEARS (This is the step you wanted)
run_df.sort_values(by='year', inplace=True)
# Sorts year from 2023 -> 2000
run_df.sort_values(by='year', ascending=False, inplace=True)
run_df.sort_values(by='year', inplace=True)


# 2. THE FIX: Create "Invisible" Placeholders
# We force every Year/Marathon/Gender combo to exist so Plotly sees them immediately.
# -------------------------------------------------------------------------
# Get lists of all unique categories
years = run_df['year'].unique()
marathons = run_df['marathon'].unique()
genders = run_df['gender'].dropna().unique() # Ensure we get Male/Female

# Create a "Skeleton" dataframe of every possible combination
idx = pd.MultiIndex.from_product([years, marathons, genders], names=['year', 'marathon', 'gender'])
skeleton_df = pd.DataFrame(index=idx).reset_index()

# Merge your real data onto this skeleton
# This keeps real data real, but adds "Empty" rows where data is missing
df_padded = pd.merge(skeleton_df, run_df, on=['year', 'marathon', 'gender'], how='left')

# CRITICAL STEP: Fill missing 'country' for the empty rows
# We need to give the empty rows a valid X-axis position (e.g., "USA") 
# so Plotly draws the trace. The dot will be invisible because 'Time' is still NaN.
fallback_country = run_df['country'].dropna().iloc[0] # Just picks 'USA' or 'Kenya'
df_padded['country'] = df_padded['country'].fillna(fallback_country)
# -------------------------------------------------------------------------

# 3. GENERATE THE GRAPH (Using the padded data)
# Calculate fixed range so axes don't jump
min_y = run_df['Time_Minutes'].min() - 2
max_y = run_df['Time_Minutes'].max() + 2

fig = px.scatter(df_padded, 
                 x="country", 
                 y="Time_Minutes", 
                 animation_frame="year", 
                 color="marathon", 
                 symbol="gender", 
                 hover_name="winner",
                 
                 # Force the X-Axis to show ALL countries (even if not in the 1st year)
                 category_orders={"country": sorted(list(run_df['country'].dropna().unique()))},
                 
                 range_y=[max_y, min_y], # Reversed so Faster is Higher
                 size_max=15,
                 title="Winning Times Distribution by Country (Sorted & Fixed)",
                 labels={
                     "country": "Country of Winner", 
                     "Time_Minutes": "Winning Time (Minutes)",
                     "marathon": "Event"
                 })

fig.show()